In [1]:
! wget https://storage.yandexcloud.net/ds-ods/files/files/77dd3242/train_annotations.json
! wget https://storage.yandexcloud.net/ds-ods/files/files/edd91118/train1.zip
! wget https://storage.yandexcloud.net/ds-ods/files/files/e5a98368/train2.zip
! wget https://storage.yandexcloud.net/ds-ods/files/files/a95eacf7/train3.zip
! wget https://storage.yandexcloud.net/ds-ods/files/files/a9a3642d/train4.zip
! wget https://storage.yandexcloud.net/ds-ods/files/files/cbdba63e/val_annotations.json
! wget https://storage.yandexcloud.net/ds-ods/files/files/adacb253/val.zip
! wget https://storage.yandexcloud.net/ds-ods/files/files/2ad601fd/test.zip

--2025-02-06 04:00:19--  https://storage.yandexcloud.net/ds-ods/files/files/77dd3242/train_annotations.json
Resolving storage.yandexcloud.net (storage.yandexcloud.net)... 213.180.193.243, 2a02:6b8::1d9
Connecting to storage.yandexcloud.net (storage.yandexcloud.net)|213.180.193.243|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 362313284 (346M) [application/json]
Saving to: ‘train_annotations.json’

train_annotations.j 100%[===================>] 345.53M  12.4MB/s    in 26s     

2025-02-06 04:00:46 (13.5 MB/s) - ‘train_annotations.json’ saved [362313284/362313284]

--2025-02-06 04:00:46--  https://storage.yandexcloud.net/ds-ods/files/files/edd91118/train1.zip
Resolving storage.yandexcloud.net (storage.yandexcloud.net)... 213.180.193.243, 2a02:6b8::1d9
Connecting to storage.yandexcloud.net (storage.yandexcloud.net)|213.180.193.243|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 974593914 (929M) [application/x-zip-compressed]
Saving to:

In [2]:
! unzip train1.zip
! unzip train2.zip
! unzip train3.zip
! unzip train4.zip
! unzip val.zip
! unzip test.zip

Archive:  train1.zip
   creating: train1/
  inflating: train1/00125bfe8be15839ddd18af48b962045.JPG  
  inflating: train1/0007639bc8147f910fd8c63c7bc494d5.JPG  
  inflating: train1/0020f7372b7b48c2882e7c7abe26007f.JPG  
  inflating: train1/001512343e474eaf929505791f71d195.JPG  
  inflating: train1/001c9942d5a53aad0257095fdb37e125.JPG  
  inflating: train1/009d1e872a83265eddc2f97e1585cf93.JPG  
  inflating: train1/00943ba5a351232214bd9fdaa7f98036.JPG  
  inflating: train1/0058b70bf050741bd639b47357051ca7.JPG  
  inflating: train1/00ade26023d5b9d129c334154d0b4b26.JPG  
  inflating: train1/00b1e81fd1dc4a6c50a869e99fefc02b.JPG  
  inflating: train1/00d0be847fad29d8ec410a030e9db78a.JPG  
  inflating: train1/00b00342f6fa44ac12111aa5bf1aff06.JPG  
  inflating: train1/00a1e0d34bf0cc1e0088e4bcddda29a0.JPG  
  inflating: train1/00b0680eccbc5937adda412df7447bed.JPG  
  inflating: train1/00daa9a74e4d2439c65c12c7f553fc65.JPG  
  inflating: train1/00c5b1a40a59883c4cb29489179841a4.JPG  
  inflating: t

In [3]:
! pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 914.8/914.8 kB 21.9 MB/s eta 0:00:00


In [4]:
from ultralytics import YOLO
import os
import shutil
import contextlib
import json
from collections import defaultdict

import cv2
import pandas as pd
from PIL import Image

import glob
import os
import shutil
from pathlib import Path

import numpy as np
from PIL import ExifTags
from tqdm import tqdm
import torch

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [5]:
img_formats = ["bmp", "jpg", "jpeg", "png", "tif", "tiff", "dng"]  # acceptable image suffixes
vid_formats = ["mov", "avi", "mp4", "mpg", "mpeg", "m4v", "wmv", "mkv"]  # acceptable video suffixes

# Get orientation exif tag
for orientation in ExifTags.TAGS.keys():
    if ExifTags.TAGS[orientation] == "Orientation":
        break


def exif_size(img):
    """Returns the EXIF-corrected PIL image size as a tuple (width, height)."""
    s = img.size  # (width, height)
    try:
        rotation = dict(img._getexif().items())[orientation]
        if rotation in [6, 8]:  # rotation 270
            s = (s[1], s[0])
    except Exception:
        pass

    return s


def split_rows_simple(file="../data/sm4/out.txt"):  # from utils import *; split_rows_simple()
    """Splits a text file into train, test, and val files based on specified ratios; expects a file path as input."""
    with open(file) as f:
        lines = f.readlines()

    s = Path(file).suffix
    lines = sorted(list(filter(lambda x: len(x) > 0, lines)))
    i, j, k = split_indices(lines, train=0.9, test=0.1, validate=0.0)
    for k, v in {"train": i, "test": j, "val": k}.items():  # key, value pairs
        if v.any():
            new_file = file.replace(s, f"_{k}{s}")
            with open(new_file, "w") as f:
                f.writelines([lines[i] for i in v])


def split_files(out_path, file_name, prefix_path=""):  # split training data
    """Splits file names into separate train, test, and val datasets and writes them to prefixed paths."""
    file_name = list(filter(lambda x: len(x) > 0, file_name))
    file_name = sorted(file_name)
    i, j, k = split_indices(file_name, train=0.9, test=0.1, validate=0.0)
    datasets = {"train": i, "test": j, "val": k}
    for key, item in datasets.items():
        if item.any():
            with open(f"{out_path}_{key}.txt", "a") as file:
                for i in item:
                    file.write(f"{prefix_path}{file_name[i]}\n")


def split_indices(x, train=0.9, test=0.1, validate=0.0, shuffle=True):  # split training data
    """Splits array indices for train, test, and validate datasets according to specified ratios."""
    n = len(x)
    v = np.arange(n)
    if shuffle:
        np.random.shuffle(v)

    i = round(n * train)  # train
    j = round(n * test) + i  # test
    k = round(n * validate) + j  # validate
    return v[:i], v[i:j], v[j:k]  # return indices


def make_dirs(dir="new_dir/"):
    """Creates a directory with subdirectories 'labels' and 'images', removing existing ones."""
    dir = Path(dir)
    if dir.exists():
        shutil.rmtree(dir)  # delete dir
    for p in dir, dir / "labels", dir / "images":
        p.mkdir(parents=True, exist_ok=True)  # make dir
    return dir


def write_data_data(fname="data.data", nc=80):
    """Writes a Darknet-style .data file with dataset and training configuration."""
    lines = [
        f"classes = {nc:g}\n",
        "train =../out/data_train.txt\n",
        "valid =../out/data_test.txt\n",
        "names =../out/data.names\n",
        "backup = backup/\n",
        "eval = coco\n",
    ]

    with open(fname, "a") as f:
        f.writelines(lines)


def image_folder2file(folder="images/"):  # from utils import *; image_folder2file()
    """Generates a txt file listing all images in a specified folder; usage: `image_folder2file('path/to/folder/')`."""
    s = glob.glob(f"{folder}*.*")
    with open(f"{folder[:-1]}.txt", "w") as file:
        for l in s:
            file.write(l + "\n")  # write image list


def add_coco_background(path="../data/sm4/", n=1000):  # from utils import *; add_coco_background()
    """
    Adds COCO dataset background images to a specified folder and lists them in outb.txt; usage:

    `add_coco_background('path/', 1000)`.
    """
    p = f"{path}background"
    if os.path.exists(p):
        shutil.rmtree(p)  # delete output folder
    os.makedirs(p)  # make new output folder

    # copy images
    for image in glob.glob("../coco/images/train2014/*.*")[:n]:
        os.system(f"cp {image} {p}")

    # add to outb.txt and make train, test.txt files
    f = f"{path}out.txt"
    fb = f"{path}outb.txt"
    os.system(f"cp {f} {fb}")
    with open(fb, "a") as file:
        file.writelines(i + "\n" for i in glob.glob(f"{p}/*.*"))
    split_rows_simple(file=fb)


def create_single_class_dataset(path="../data/sm3"):  # from utils import *; create_single_class_dataset('../data/sm3/')
    """Creates a single-class version of an existing dataset in the specified path."""
    os.system(f"mkdir {path}_1cls")


def flatten_recursive_folders(path="../../Downloads/data/sm4/"):  # from utils import *; flatten_recursive_folders()
    """Flattens nested folders in 'path/images' and 'path/json' into single 'images_flat' and 'json_flat'
    directories.
    """
    idir, _jdir = f"{path}images/", f"{path}json/"
    nidir, njdir = Path(f"{path}images_flat/"), Path(f"{path}json_flat/")
    n = 0

    # Create output folders
    for p in [nidir, njdir]:
        if os.path.exists(p):
            shutil.rmtree(p)  # delete output folder
        os.makedirs(p)  # make new output folder

    for parent, dirs, files in os.walk(idir):
        for f in tqdm(files, desc=parent):
            f = Path(f)
            stem, suffix = f.stem, f.suffix
            if suffix.lower()[1:] in img_formats:
                n += 1
                stem_new = f"{n:g}_{stem}"
                image_new = nidir / (stem_new + suffix)  # converts all formats to *.jpg
                json_new = njdir / f"{stem_new}.json"

                image = parent / f
                json = Path(parent.replace("images", "json")) / str(f).replace(suffix, ".json")

                os.system(f"cp '{json}' '{json_new}'")
                os.system(f"cp '{image}' '{image_new}'")
                # cv2.imwrite(str(image_new), cv2.imread(str(image)))

    print(f"Flattening complete: {n:g} jsons and images")

def coco91_to_coco80_class():  # converts 80-index (val2014) to 91-index (paper)
    """Converts COCO 91-class index (paper) to 80-class index (2014 challenge)."""
    return [
        0,
        1,
        2,
        3,
        4,
        5,
        6,
        7,
        8,
        9,
        10,
        None,
        11,
        12,
        13,
        14,
        15,
        16,
        17,
        18,
        19,
        20,
        21,
        22,
        23,
        None,
        24,
        25,
        None,
        None,
        26,
        27,
        28,
        29,
        30,
        31,
        32,
        33,
        34,
        35,
        36,
        37,
        38,
        39,
        None,
        40,
        41,
        42,
        43,
        44,
        45,
        46,
        47,
        48,
        49,
        50,
        51,
        52,
        53,
        54,
        55,
        56,
        57,
        58,
        59,
        None,
        60,
        None,
        None,
        61,
        None,
        62,
        63,
        64,
        65,
        66,
        67,
        68,
        69,
        70,
        71,
        72,
        None,
        73,
        74,
        75,
        76,
        77,
        78,
        79,
        None,
    ]

def copy_images(dst_path, src_paths):
    if not os.path.exists(dst_path):
        os.makedirs(dst_path)
    for folder_name in src_paths:
        for file_name in tqdm(os.listdir(folder_name)):
            src = os.path.join(folder_name, file_name)
            dst = os.path.join(dst_path, file_name)
            shutil.copy(src, dst)

def min_index(arr1, arr2):
    """
    Find a pair of indexes with the shortest distance.

    Args:
        arr1: (N, 2).
        arr2: (M, 2).

    Return:
        a pair of indexes(tuple).
    """
    dis = ((arr1[:, None, :] - arr2[None, :, :]) ** 2).sum(-1)
    return np.unravel_index(np.argmin(dis, axis=None), dis.shape)

def merge_multi_segment(segments):
    """
    Merge multi segments to one list. Find the coordinates with min distance between each segment, then connect these
    coordinates with one thin line to merge all segments into one.

    Args:
        segments(List(List)): original segmentations in coco's json file.
            like [segmentation1, segmentation2,...],
            each segmentation is a list of coordinates.
    """
    s = []
    segments = [np.array(i).reshape(-1, 2) for i in segments]
    idx_list = [[] for _ in range(len(segments))]

    # record the indexes with min distance between each segment
    for i in range(1, len(segments)):
        idx1, idx2 = min_index(segments[i - 1], segments[i])
        idx_list[i - 1].append(idx1)
        idx_list[i].append(idx2)

    # use two round to connect all the segments
    for k in range(2):
        # forward connection
        if k == 0:
            for i, idx in enumerate(idx_list):
                # middle segments have two indexes
                # reverse the index of middle segments
                if len(idx) == 2 and idx[0] > idx[1]:
                    idx = idx[::-1]
                    segments[i] = segments[i][::-1, :]

                segments[i] = np.roll(segments[i], -idx[0], axis=0)
                segments[i] = np.concatenate([segments[i], segments[i][:1]])
                # deal with the first segment and the last one
                if i in [0, len(idx_list) - 1]:
                    s.append(segments[i])
                else:
                    idx = [0, idx[1] - idx[0]]
                    s.append(segments[i][idx[0] : idx[1] + 1])

        else:
            for i in range(len(idx_list) - 1, -1, -1):
                if i not in [0, len(idx_list) - 1]:
                    idx = idx_list[i]
                    nidx = abs(idx[1] - idx[0])
                    s.append(segments[i][nidx:])
    return s

def convert_coco_json(json_dir="../coco/annotations/", use_segments=False, cls91to80=False):
    """Converts COCO JSON format to YOLO label format, with options for segments and class mapping."""
    save_dir = make_dirs('dataset')  # output directory
    coco80 = coco91_to_coco80_class()

    # Import json
    for json_file in sorted(Path(json_dir).resolve().glob("*.json")):
        fn = Path(save_dir) / "labels" / json_file.stem.split("_")[0]  # folder name
        fn.mkdir()
        with open(json_file) as f:
            data = json.load(f)

        # Create image dict
        images = {"{:g}".format(x["id"]): x for x in data["images"]}
        # Create image-annotations dict
        imgToAnns = defaultdict(list)
        for ann in data["annotations"]:
            imgToAnns[ann["image_id"]].append(ann)

        # Write labels file
        for img_id, anns in tqdm(imgToAnns.items(), desc=f"Annotations {json_file}"):
            img = images[f"{img_id:g}"]
            h, w, f = img["height"], img["width"], img["file_name"]

            bboxes = []
            segments = []
            for ann in anns:
                if ann["iscrowd"]:
                    continue
                # The COCO box format is [top left x, top left y, width, height]
                box = np.array(ann["bbox"], dtype=np.float64)
                box[:2] += box[2:] / 2  # xy top-left corner to center
                box[[0, 2]] /= w  # normalize x
                box[[1, 3]] /= h  # normalize y
                if box[2] <= 0 or box[3] <= 0:  # if w <= 0 and h <= 0
                    continue

                cls = coco80[ann["category_id"]] if cls91to80 else ann["category_id"]  # class
                box = [cls] + box.tolist()
                if box not in bboxes:
                    bboxes.append(box)
                # Segments
                if use_segments:
                    if len(ann["segmentation"]) > 1:
                        s = merge_multi_segment(ann["segmentation"])
                        s = (np.concatenate(s, axis=0) / np.array([w, h])).reshape(-1).tolist()
                    else:
                        s = [j for i in ann["segmentation"] for j in i]  # all segments concatenated
                        s = (np.array(s).reshape(-1, 2) / np.array([w, h])).reshape(-1).tolist()
                    s = [cls] + s
                    if s not in segments and len(s) >= 7:
                        segments.append(s)

            # Write
            with open((fn / f).with_suffix(".txt"), "a") as file:
                for i in range(len(segments)):
                    line = (*(segments[i] if use_segments else bboxes[i]),)  # cls, box or segmentsi+1 == len(bboxes) else '')
                    file.write(("%g " * len(line)).rstrip() % line + ("\n" if i+1 != len(bboxes) else '') )

    src_paths = ["/kaggle/working/train1",
                "/kaggle/working/train2",
                "/kaggle/working/train3",
                "/kaggle/working/train4"]
    copy_images('dataset/train/images', src_paths)
    copy_images('dataset/val/images', ['val'])

convert_coco_json('/kaggle/working/', use_segments=True)

Annotations /kaggle/working/train_annotations.json: 100%|██████████| 16631/16631 [00:16<00:00, 1016.33it/s]
100%|██████████| 8557/8557 [00:02<00:00, 3612.75it/s]


In [6]:
copy_images('dataset/train/labels', ['dataset/labels/train'])
copy_images('dataset/val/labels', ['dataset/labels/val'])

100%|██████████| 8557/8557 [00:00<00:00, 8560.97it/s]


In [7]:
! rm -rf train1
! rm -rf train2
! rm -rf train3
! rm -rf train4
! rm -rf train
! rm -rf val
! rm test.zip
! rm train1.zip
! rm train2.zip
! rm train3.zip
! rm train4.zip
! rm val.zip

In [8]:
def move_files(src_dir, dst_dir, file_extension, percentage=0.33):
    # Получаем список всех файлов в исходной директории с нужным расширением
    files = [f for f in os.listdir(src_dir) if f.endswith(file_extension)]
    # Сортируем файлы (по имени или любому другому критерию)
    files.sort()
    
    # Вычисляем количество файлов, которые нужно переместить
    num_files_to_move = int(len(files) * percentage)
    
    # Перемещаем файлы
    for file_name in files[:num_files_to_move]:
        src_file = os.path.join(src_dir, file_name)
        dst_file = os.path.join(dst_dir, file_name)
        
        # Копируем файл в новую директорию
        shutil.move(src_file, dst_file)
        print(f"Перемещен файл: {file_name}")

# Определение путей к папкам
images_src_dir = '/kaggle/working/dataset/val/images'
images_dst_dir = '/kaggle/working/dataset/train/images'

labels_src_dir = '/kaggle/working/dataset/val/labels'
labels_dst_dir = '/kaggle/working/dataset/train/labels'

# Убедитесь, что целевые папки существуют
os.makedirs(images_dst_dir, exist_ok=True)
os.makedirs(labels_dst_dir, exist_ok=True)

# Перемещаем изображения
move_files(images_src_dir, images_dst_dir, '.JPG')  # Или другой формат изображений, например '.png'

# Перемещаем текстовые файлы
move_files(labels_src_dir, labels_dst_dir, '.txt')

Перемещен файл: 000c788d23390b776a4743e682b0d8ec.JPG
Перемещен файл: 0016fe0a911e54990aa9337dff70fc85.JPG
Перемещен файл: 003208ee2573c54609fb1fcecd0b4641.JPG
Перемещен файл: 00327d263a22c44896052297c819fc6e.JPG
Перемещен файл: 003cbee8730202726cf490e31bb1a9a6.JPG
Перемещен файл: 004483cabd416be17f779c70d4b25e51.JPG
Перемещен файл: 0044d1c419c2650ce319e408f6d30513.JPG
Перемещен файл: 004896f061bf8f5b48c97439ed63867c.JPG
Перемещен файл: 0055f63e875807916e1545d5133638af.JPG
Перемещен файл: 0057cc4a5accd336895a82f2011a4bd0.JPG
Перемещен файл: 005d82d8ea87eccd2ae4badbed89e723.JPG
Перемещен файл: 005ed1f7c65b80444a830f647336b4a4.JPG
Перемещен файл: 006e8e9c1f0eee1d44ee19bb3800157a.JPG
Перемещен файл: 006f2779351c44386928c08f17a039a6.JPG
Перемещен файл: 0071c98c71f9879bdd3c25f55e52c237.JPG
Перемещен файл: 007da86d9791ed977c1060f4919c536c.JPG
Перемещен файл: 00b2ff1e39a2e38b3e8c9f288eb672dc.JPG
Перемещен файл: 00b601d2138f140a78f90672599a0bd6.JPG
Перемещен файл: 00bad106b7981e0aa1f532b2601e8d

In [9]:
import yaml

data = {
    'train': '/kaggle/working/dataset/train',  # путь к обучающим изображениям
    'val': '/kaggle/working/dataset/val',  # путь к изображениям для валидации
    'nc': 1,  # количество классов
    'names': ['Animal'],  # имена классов
    'augmentation': {  # IoU training threshold
        # anchors: 3,  # anchors per output layer (0 to ignore)
        'hsv_h': 0.015,  # image HSV-Hue augmentation (fraction)
        'hsv_s': 0.9,  # image HSV-Saturation augmentation (fraction)
        'hsv_v': 0.5,  # image HSV-Value augmentation (fraction)
        'degrees': 5.0,  # image rotation (+/- deg)
        'translate': 0.1,  # image translation (+/- fraction)
        'scale': 0.2,  # image scale (+/- gain) - MODIFIED
        'shear': 0.0,  # image shear (+/- deg)
        'perspective': 0.0,  # image perspective (+/- fraction), range 0-0.001
        'flipud': 0.0,  # image flip up-down (probability)
        'fliplr': 0.5,  # image flip left-right (probability)
        'mosaic': 0.9,  # image mosaic (probability) - MODIFIED
        'mixup': 0.2,  # image mixup (probability)
        'copy_paste': 0.0,  # segment copy-paste (probability),
        'noise': 0.05,
        'elastic_transform': True,  # включить эластичное преобразование
        'cutout': 0.5,  # вероятность применения cutout
        'crop': 0.1,  # вероятность случайного обрезания (например, 10%)
        'rotate': 10.0,  # угол вращения в градусах
        'amp': True
    }
}

# Сохранение данных в YAML файл
with open('data.yaml', 'w') as file:
    yaml.dump(data, file, default_flow_style=False, allow_unicode=True)

print("YAML файл успешно создан!")

YAML файл успешно создан!


In [10]:
# import torch
# import gc
# torch.cuda.empty_cache()
# gc.collect()

In [11]:
model = YOLO('yolo11x-seg.pt')
model.train(data='data.yaml',
            epochs=27,
            imgsz=224,
            batch=0.95,
            # device='0',
            name='yolo_segmentation',
            optimizer='Adam',
            lr0= 0.00001,  # initial learning rate (SGD=1E-2, Adam=1E-3)
            lrf= 0.1,  # final OneCycleLR learning rate (lr0 * lrf)
            momentum= 0.937,  # SGD momentum/Adam beta1
            weight_decay= 0.001,  # optimizer weight decay 5e-4
            warmup_epochs= 0.0,  # warmup epochs (fractions ok) - MODIFIED
            warmup_momentum= 0.8,  # warmup initial momentum
            warmup_bias_lr= 0.1,  # warmup initial bias lr
            save_period=5,
            task='segmentation',   
)
# !yolo train model='yolo11x-seg.pt' data='data.yaml' epochs=50 imgsz=640 batch=64 optimizer='Adam' lr0=0.00005 lrf=0.1 momentum=0.937 weight_decay=0.0005 warmup_epochs=0.0 warmup_momentum=0.8 warmup_bias_lr=0.1 save_period=5 task='segment' device=[0,1,2,3]

100%|██████████| 119M/119M [00:00<00:00, 153MB/s] 


Ultralytics 8.3.72 🚀 Python-3.10.12 torch-2.5.1+cu121 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: task=segment, mode=train, model=yolo11x-seg.pt, data=data.yaml, epochs=27, time=None, patience=100, batch=0.95, imgsz=224, save=True, save_period=5, cache=False, device=None, workers=8, project=None, name=yolo_segmentation, exist_ok=False, pretrained=True, optimizer=Adam, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True, show_boxe

100%|██████████| 755k/755k [00:00<00:00, 22.5MB/s]


Overriding model.yaml nc=80 with nc=1

                   from  n    params  module                                       arguments                     
  0                  -1  1      2784  ultralytics.nn.modules.conv.Conv             [3, 96, 3, 2]                 
  1                  -1  1    166272  ultralytics.nn.modules.conv.Conv             [96, 192, 3, 2]               
  2                  -1  2    389760  ultralytics.nn.modules.block.C3k2            [192, 384, 2, True, 0.25]     
  3                  -1  1   1327872  ultralytics.nn.modules.conv.Conv             [384, 384, 3, 2]              
  4                  -1  2   1553664  ultralytics.nn.modules.block.C3k2            [384, 768, 2, True, 0.25]     
  5                  -1  1   5309952  ultralytics.nn.modules.conv.Conv             [768, 768, 3, 2]              
  6                  -1  2   5022720  ultralytics.nn.modules.block.C3k2            [768, 768, 2, True]           
  7                  -1  1   5309952  ultralytics

100%|██████████| 5.35M/5.35M [00:00<00:00, 99.8MB/s]


...

                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 56/56 [00:48<00:00,  1.15it/s]


                   all       5734       6380      0.978      0.942      0.976      0.882      0.974      0.925      0.962      0.759


/usr/local/lib/python3.10/dist-packages/matplotlib/colors.py:721: RuntimeWarning: invalid value encountered in less
  xa[xa < 0] = -1
/usr/local/lib/python3.10/dist-packages/matplotlib/colors.py:721: RuntimeWarning: invalid value encountered in less
  xa[xa < 0] = -1


Speed: 0.0ms preprocess, 3.0ms inference, 0.0ms loss, 0.8ms postprocess per image
Results saved to runs/segment/yolo_segmentation


ultralytics.utils.metrics.SegmentMetrics object with attributes:

ap_class_index: array([0])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x7e38a4ffe6e0>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)', 'Precision-Recall(M)', 'F1-Confidence(M)', 'Precision-Confidence(M)', 'Recall-Confidence(M)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041, 

In [12]:
from tqdm import tqdm
import os
import cv2
import json
import numpy as np
from ultralytics import YOLO
import pycocotools.mask

test_folder = "test"  # Папка с тестовыми изображениями
output_folder = "output"  # Папка для сохранения результатов
os.makedirs(output_folder, exist_ok=True)

# Список для хранения предсказаний в нужном формате
predictions = []

# Обработка изображений
for file_name in tqdm(os.listdir(test_folder)):
    image_path = os.path.join(test_folder, file_name)
    image = cv2.imread(image_path)
    height, width = image.shape[:2]  # Определяем размеры изображения

    # Выполнение предсказания
    results = model(image_path)

    for result in results:
        boxes = result.boxes.xyxy.cpu().numpy()  # Bounding boxes [x1, y1, x2, y2]
        scores = result.boxes.conf.cpu().numpy()  # Уверенность
        classes = result.boxes.cls.cpu().numpy().astype(int)  # Классы объектов
        masks = result.masks.data.cpu().numpy() if result.masks else None  # Маски (если доступны)

        for i in range(len(boxes)):
            x1, y1, x2, y2 = boxes[i]
            width_bbox = x2 - x1
            height_bbox = y2 - y1
            bbox = [float(x1), float(y1), float(width_bbox), float(height_bbox)]  # Преобразование bbox
            score = float(scores[i])  # Преобразование уверенности
            category_id = 1  # Преобразование категории

            # Форматирование RLE для сегментации
            if masks is not None:
                rle = pycocotools.mask.encode(np.asfortranarray(masks[i].astype(np.uint8)))
                segmentation = {
                    "size": [height, width],
                    "counts": rle["counts"].decode("utf-8")
                }
            else:
                segmentation = {
                    "size": [height, width],
                    "counts": ""
                }

            # Добавление предсказания в список
            predictions.append({
                "image_name": file_name,
                "category_id": category_id,
                "bbox": bbox,
                "score": score,
                "segmentation": segmentation
            })

# Сохранение предсказаний в JSON
predictions_file = os.path.join(output_folder, "super_secret_submission.json")
with open(predictions_file, "w") as f:
    json.dump(predictions, f, indent=4)

print(f"Обработка завершена. Результаты сохранены в папке: {output_folder}")

  0%|          | 0/9074 [00:00<?, ?it/s]


image 1/1 /kaggle/working/test/ed85647577a289e3ae619e6fddf54165.JPG: 128x224 1 Animal, 56.0ms
Speed: 0.6ms preprocess, 56.0ms inference, 4.9ms postprocess per image at shape (1, 3, 128, 224)


  0%|          | 1/9074 [00:00<2:11:56,  1.15it/s]


image 1/1 /kaggle/working/test/304c78306e73fd55b3e4fa657e249492.JPG: 128x224 1 Animal, 25.2ms
Speed: 0.5ms preprocess, 25.2ms inference, 3.0ms postprocess per image at shape (1, 3, 128, 224)

image 1/1 /kaggle/working/test/ad9d825e921874e868d8380a9efa003a.JPG: 128x224 1 Animal, 23.7ms
Speed: 0.5ms preprocess, 23.7ms inference, 2.8ms postprocess per image at shape (1, 3, 128, 224)


  0%|          | 3/9074 [00:00<40:42,  3.71it/s]  

...


image 1/1 /kaggle/working/test/4192b1829662a60584b3c20d038f1176.JPG: 128x224 1 Animal, 19.5ms
Speed: 0.5ms preprocess, 19.5ms inference, 2.7ms postprocess per image at shape (1, 3, 128, 224)

image 1/1 /kaggle/working/test/0bd1abdec5b367f8f53e3ab3808dee7b.JPG: 128x224 1 Animal, 19.5ms
Speed: 0.4ms preprocess, 19.5ms inference, 2.7ms postprocess per image at shape (1, 3, 128, 224)

image 1/1 /kaggle/working/test/0191d789ffec5d54466b7fcba73dabac.JPG: 128x224 1 Animal, 19.4ms
Speed: 0.5ms preprocess, 19.4ms inference, 2.7ms postprocess per image at shape (1, 3, 128, 224)


100%|█████████▉| 9072/9074 [07:41<00:00, 19.57it/s]


image 1/1 /kaggle/working/test/b16aa9c8a7a06da0f5947eb29b68f575.JPG: 128x224 1 Animal, 19.5ms
Speed: 0.4ms preprocess, 19.5ms inference, 2.7ms postprocess per image at shape (1, 3, 128, 224)

image 1/1 /kaggle/working/test/0b3d0753f522e260b66aef3ef825796f.JPG: 128x224 1 Animal, 19.4ms
Speed: 0.4ms preprocess, 19.4ms inference, 2.8ms postprocess per image at shape (1, 3, 128, 224)


100%|██████████| 9074/9074 [07:41<00:00, 19.66it/s]


Обработка завершена. Результаты сохранены в папке: output
